In [1]:
import sys
import os

sys.path.append(os.path.abspath("../src"))
PROJECT_ROOT = os.getenv("PROJECT_ROOT")

In [2]:
from recommender.data_processors.mastery_features_processor import MasteryFeaturesProcessor
from recommender.data_loaders.summoner_match_loader import SummonerMatchLoader
from recommender.utils.riot_api_helper import RiotApiHelper
from recommender.utils.map_helper import MapHelper

mfp = MasteryFeaturesProcessor()
rah = RiotApiHelper()
sml = SummonerMatchLoader()
mh = MapHelper()

In [3]:
from recommender.utils.data_utils import ChampionsFeaturesDataset
from recommender.utils.data_utils import MultiEpochsDataLoader
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import OrdinalEncoder

In [9]:
df, le_user, le_encoder = await mfp.async_load_encoded_ratings()
categorical_cols = ["summoner_rank", "summoner_lane", "champ_attack_type", "champ_adaptive_type"]
df[categorical_cols] = OrdinalEncoder().fit_transform(df[categorical_cols]).astype(int)

In [10]:
train_df, test_df = train_test_split(df, test_size=0.2)
train_dataset = ChampionsFeaturesDataset(train_df)
test_dataset = ChampionsFeaturesDataset(test_df)

In [15]:
train_loader = MultiEpochsDataLoader(train_dataset, batch_size=20, shuffle=True)
test_loader = MultiEpochsDataLoader(test_dataset, batch_size=20, shuffle=True)

In [16]:
from recommender.filters.two_tower import TwoTowerModel
import torch
import torch.nn as nn

In [17]:
train_df

puuid champ_name  \
86443   LjzLpF709bTO9WVqeE0uagg4ojGRiJKO1YZkmoJ9rdABTe...     Samira   
132401  ZjG_VdpU--7cDeg-IAn4Kwga_O8AXE-VRlWEBTWExRTx8V...   Nocturne   
144064  lKiOb1q4mevGxEWN72TJmDk35qnSNhaN04v_yJSUAC9B0-...    Skarner   
3003    kssc4Zzl-SjQsUPC5AKz35MSQoEhCJ4tj91ZhUyev3rMNp...     Akshan   
39204   nkULuyZY7HjzrTKZzg-jZpq5rPPM_WV88Kom9ql2YZ76hq...      Janna   
...                                                   ...        ...   
80045   4R7gu6gmXI2oRfRzUp0ZMtz_01DjSQ5Whh4fOAFOVtm330...     RekSai   
11164   _IuTZTAZL7ae4L7HmNNB0mIamvIN_DEVipkrwtf33Pk9EC...     Aurora   
77400   --EEhXPKpjfGXqRUXQeFUIrad-z3jgjyrwQj6Z49G4zWAK...      Quinn   
105607  U_8D4Yuj9u6k7idWU36fR37ryEAxLxV9cEhwXDWRCPDuwM...     Twitch   
74206   DuulpSb4JNiOVbsbvDvdAVWmq32M1sOxSz9mMpHWauymCt...   Pantheon   

           rating  user_id  champ_id  summoner_rank  summoner_lane  \
86443    4.118188      302       114              2              2   
132401   4.659198      480        94              5              2   
144064   0.000000      653       125              7              2   
3003     1.995321      643         3              6              0   
39204   17.528258      688        49              2              1   
...           ...      ...       ...            ...            ...   
80045    2.076365       63       106              2              2   
11164    0.000000      489        12              6              3   
77400    3.460554        0       103              5              1   
105607   0.578342      402       142              6              2   
74206    9.658480      191        99              1              1   

        champ_attack_type  champ_adaptive_type  
86443                   1                    1  
132401                  0                    1  
144064                  0                    1  
3003                    1                    1  
39204                   1                    0  
...                   ...                  ...  
80045                   0                    1  
11164                   1                    0  
77400                   1                    1  
105607                  1                    1  
74206                   0                    1  

[116960 rows x 9 columns]

In [ ]:
model = TwoTowerModel()
optimizer = torch.optim.Adam(model.parameters(), lr=1e-3)
# To update to negative sampling
criterion = nn.MSELoss()
for epoch in range(1):
    model.train()
    total_loss = 0
    for summoner_factors, champ_factors, ratings in train_loader:
        optimizer.zero_grad()
        preds = model(summoner_factors, champ_factors)
        loss = criterion(preds, ratings)
        loss.backward()
        optimizer.step()
        total_loss += loss.item()
    print(f"Epoch {epoch+1}, Loss: {total_loss / len(train_loader)}")   
        

[tensor([0, 0, 0, 1, 1]), tensor([0, 1, 1, 1, 1])]
[tensor([1, 1, 0, 1, 1]), tensor([1, 1, 1, 1, 0])]
[tensor([0, 0, 0, 0, 1]), tensor([1, 1, 1, 1, 1])]
[tensor([0, 1, 0, 0, 1]), tensor([1, 1, 0, 0, 0])]
[tensor([0, 1, 1, 1, 1]), tensor([1, 0, 1, 1, 0])]
[tensor([0, 0, 1, 0, 0]), tensor([1, 1, 0, 1, 1])]
[tensor([0, 0, 0, 1, 0]), tensor([1, 0, 1, 0, 0])]
[tensor([0, 0, 0, 0, 0]), tensor([0, 1, 1, 0, 0])]
[tensor([1, 1, 0, 1, 0]), tensor([1, 1, 1, 1, 1])]
[tensor([1, 0, 1, 1, 1]), tensor([0, 0, 1, 0, 0])]
[tensor([0, 1, 1, 0, 0]), tensor([0, 0, 1, 1, 1])]
[tensor([1, 1, 1, 1, 1]), tensor([1, 0, 1, 0, 0])]
[tensor([1, 0, 0, 1, 1]), tensor([1, 1, 1, 0, 0])]
[tensor([1, 0, 0, 1, 0]), tensor([1, 1, 0, 1, 1])]
[tensor([1, 0, 1, 1, 1]), tensor([1, 1, 0, 0, 1])]
[tensor([1, 1, 0, 1, 0]), tensor([0, 0, 1, 0, 1])]
[tensor([0, 1, 1, 1, 0]), tensor([1, 0, 0, 0, 0])]
[tensor([0, 1, 1, 0, 0]), tensor([0, 0, 1, 1, 1])]
[tensor([1, 0, 0, 1, 0]), tensor([0, 1, 0, 0, 1])]
[tensor([1, 1, 0, 1, 1]), tenso

In [ ]:
# Step 1: Build the df with column of lets say mode rank, mode lanes, roles, attack_types
# Step 2: Make train and test loader using TwoTowerChampionDataset
# Step 3: iterate for user_feattures, champ_features, rating in loader: preds = model(user_features, champ_features)

In [ ]:
puuid = "_2dRYSt03dHrJrRDcYImk2_umcnVSo8i-1WMun-j8YAFYk9CzauMu7WjQ8IJCY_RDWMopccQI_qfcw"
match_ids = rah.get_player_matches(puuid)